# 파이토치 에서의 분산 모델 Inference
- Infernce를 위한 Pretrained 모델을 준비
- databricks-dataset 에서 부터 Spark DataFrames로 로드
- Pandas UDF로 모델 Inference를 한다.

In [0]:
# Arrow 를 Enable 한다.
spark.conf.set("spark.sql.execution.arrow.enabled", "true")
spark.conf.set("spark.sql.execution.arrow.maxRecordsPerBatch", "64")

In [0]:
import os
import io
import shutil
import uuid
from typing import Iterator, Tuple

import pandas as pd 

import torch
from torch.utils.data import Dataset
from torchvision import datasets, models, transforms
from torchvision.datasets.folder import default_loader

from pyspark.sql.functions import col, pandas_udf
from pyspark.sql.types import ArrayType, FloatType
from PIL import Image

In [0]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [0]:
print(f"device - {device}")

device - cpu

## Inference를 위한 모델 준비
ResNet50 모델을 driver node에 Load하고 모델 state를 broadcast 한다.

In [0]:
model_state = models.resnet18(pretrained=True).state_dict()
bc_model_state = sc.broadcast(model_state)

def get_model_for_eval():
  # broadcast 한 모델 getter()
  model = models.resnet18(pretrained=True)
  model.load_state_dict(bc_model_state.value)
  model.eval()
  return model

## Spark DataFrames로 데이터를 로드

In [0]:
%fs ls /databricks-datasets/flower_photos

path name size dbfs:/databricks-datasets/flower_photos/LICENSE.txt LICENSE.txt 418049 dbfs:/databricks-datasets/flower_photos/README.md README.md 1157 dbfs:/databricks-datasets/flower_photos/daisy/ daisy/ 0 dbfs:/databricks-datasets/flower_photos/dandelion/ dandelion/ 0 dbfs:/databricks-datasets/flower_photos/roses/ roses/ 0 dbfs:/databricks-datasets/flower_photos/sunflowers/ sunflowers/ 0 dbfs:/databricks-datasets/flower_photos/tulips/ tulips/ 0

In [0]:
files_df = spark.read.format("binaryFile") \
  .option("recursiveFileLookup", "true") \
  .option("pathGlobFilter", "*.jpg") \
  .load("/databricks-datasets/flower_photos") \
  .repartition(4)

In [0]:
display(files_df.limit(5))

path modificationTime length content dbfs:/databricks-datasets/flower_photos/tulips/3011223301_09b4e3edb7.jpg 2019-12-11T22:18:33.000+0000 235266 /9j/4AAQSkZJRgABAQEASABIAAD/4gxYSUNDX1BST0ZJTEUAAQEAAAxITGlubwIQAABtbnRyUkdCIFhZWiAHzgACAAkABgAxAABhY3NwTVNGVAAAAABJRUMgc1JHQgAAAAAAAAAAAAAAAAAA9tYAAQAAAADTLUhQICAAAAAAAAA= (truncated) dbfs:/databricks-datasets/flower_photos/sunflowers/8543642705_b841b0e5f6.jpg 2019-12-11T22:18:12.000+0000 235856 /9j/4AAQSkZJRgABAQEASABIAAD/4gxYSUNDX1BST0ZJTEUAAQEAAAxITGlubwIQAABtbnRyUkdCIFhZWiAHzgACAAkABgAxAABhY3NwTVNGVAAAAABJRUMgc1JHQgAAAAAAAAAAAAAAAAAA9tYAAQAAAADTLUhQICAAAAAAAAA= (truncated) dbfs:/databricks-datasets/flower_photos/sunflowers/4932735362_6e1017140f.jpg 2019-12-11T22:18:00.000+0000 277326 /9j/4AAQSkZJRgABAQEASABIAAD/2wBDAAEBAQEBAQEBAQEBAQECAgMCAgICAgQDAwIDBQQFBQUEBAQFBgcGBQUHBgQEBgkGBwgICAgIBQYJCgkICgcICAj/2wBDAQEBAQICAgQCAgQIBQQFCAgICAgICAgICAgICAgICAgICAg= (truncated) dbfs:/databricks-datasets/flower_photos/daisy/5874818796_3efbb8769d.jpg 2019-12-11T22:16:31.000+0000 229395 /9j/4AAQSkZJRgABAQEASABIAAD/4gxYSUNDX1BST0ZJTEUAAQEAAAxITGlubwIQAABtbnRyUkdCIFhZWiAHzgACAAkABgAxAABhY3NwTVNGVAAAAABJRUMgc1JHQgAAAAAAAAAAAAAAAAAA9tYAAQAAAADTLUhQICAAAAAAAAA= (truncated) dbfs:/databricks-datasets/flower_photos/sunflowers/6140892289_92805cc590.jpg 2019-12-11T22:18:07.000+0000 243637 /9j/4AAQSkZJRgABAQEASABIAAD/4iH8SUNDX1BST0ZJTEUAAQEAACHsTktPTgIgAABtbnRyUkdCIFhZWiAH2QACABQAEQAHAAphY3NwQVBQTAAAAABub25lAAAAAQAAAAAAAAAAAAAAAAAA9tYAAQAAAADTLQAAAAAAAAAAAAA= (truncated)

## Pandas UDF 를 사용해서 모델 inference

In [0]:
# 커스텀 PyTorch 데이터셋 클래스를 생성한다.
class ImageDataset(Dataset):
  def __init__(self, contents, transform=None):
    self.contents = contents
    self.transform = transform
    
  def __len__(self):
    return len(self.contents)
  
  def __getitem__(self, index):
    return self._preprocess(self.contents[index])  
  
  def _preprocess(self, content):
    image = Image.open(io.BytesIO(content))
    return self.transform(image)

In [0]:
# 모델 inference를 위해 함수를 정의
@pandas_udf(ArrayType(FloatType()))
def predict_batch_udf(contents: pd.Series) -> pd.Series:

  transform = transforms.Compose([
    transforms.Resize(224),
    transforms.CenterCrop(224),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406],
                       std=[0.229, 0.224, 0.225])
  ])
  
  images = ImageDataset(contents=contents, transform=transform)
  loader = torch.utils.data.DataLoader(images, batch_size=500, num_workers=8)
  
  model = get_model_for_eval()
  model.to(device)
  
  all_predictions = []
  with torch.no_grad():
    for batch in loader:
      predictions = list(model(batch.to(device)).cpu().numpy())
      for prediction in predictions:
        all_predictions.append(prediction)
        
  return pd.Series(all_predictions)

In [0]:
# 모델 inference를 하고 Parquet 파일로 inference 결과를 저장
predictions_df = files_df.select(col('content'), predict_batch_udf(col('content')).alias("prediction"))

## Pretrain 모델의 Output Size는 1000개
``` python
resnet.fc = nn.Linear(resnet.fc.in_features, n_features)
torch.save(resnet, 'model.pth')
model = torch.load('model.pth')

inp = torch.randn(1, 3, 224, 224)
out = model(inp)
print(out.size()) -> torch.Size([1, 100])
```

In [0]:
display(predictions_df)

content prediction /9j/4AAQSkZJRgABAQEASABIAAD/4iH8SUNDX1BST0ZJTEUAAQEAACHsTktPTgIgAABtbnRyUkdCIFhZWiAH2QACABQAEQAHAAphY3NwQVBQTAAAAABub25lAAAAAQAAAAAAAAAAAAAAAAAA9tYAAQAAAADTLQAAAAAAAAAAAAA= (truncated) List(1.7725176, 1.5770736, -2.6005592, -4.905384, -3.3790333, -1.9383128, -0.60205895, -0.197613, -0.18928075, 2.6218255, -0.50234866, 2.9826248, -0.35017857, -1.4919655, 0.6217473, 0.64147174, -1.8989611, -1.0708106, 0.73241657, -2.5698917, -0.46360493, 1.3014597, 1.9864749, -0.10609645, 3.4643447, 4.594158, 2.380334, 1.6286986, 2.528562, -3.2339952, 2.0352037, -1.0854582, -0.8066826, -1.7890975, 0.1262632, 1.740254, 2.0371528, 3.2759664, -1.2690675, 0.19193923, -0.44395652, -2.677982, -1.5153213, 0.49674007, -0.35637426, 3.195145, 0.62966096, 3.0667338, 0.781185, 1.3670173, 1.8256392, 0.5954966, -1.479928, -1.6697989, -0.054195225, 1.1609875, -1.3336691, -0.9130181, -0.5802858, -0.4931754, -0.99556625, 0.07373883, 1.044997, -2.4257038, 1.8397236, -2.7832828, -0.46932697, 0.51887107, -1.684916, -3.8083298, -0.26433784, -3.2416544, 2.3970397, 3.042668E-4, 2.7559204, -2.8508973, -0.42100918, 0.051429972, -1.7878013, -1.0414982, -2.5719452, -1.7337067, -0.7291219, -0.4774648, 0.8143737, 0.0065226555, -0.5673452, -2.4061995, 2.326864, 1.1267153, 1.0586907, -1.9578568, 0.12305617, 1.6415417, 0.66466516, -0.32577184, 0.6567751, -1.8466474, -4.920596, -0.917505, -2.3007884, -0.03603828, -1.9014257, 1.2262081, 0.68487847, -2.1935437, 0.15825069, 0.87938464, -1.7734747, -1.8111606, -1.6086483, -1.041224, -0.84098995, 0.83686906, 0.5676784, -1.289266, -1.9469901, -3.5954056, -0.50811917, -2.688472, -3.670728, -2.873859, -2.1177642, -3.8778353, -1.2435992, -2.4141426, -3.1271846, 0.8599884, -0.7303767, -0.48729515, -2.1587408, -0.06906229, 1.6534498, 1.0533633, 0.25611582, 1.6888733, -0.7751453, -2.138032, 0.9331051, -1.2752732, -0.9435465, -0.408939, -2.157826, -1.579575, -2.7162597, 0.064563274, -1.7323421, -2.3731158, -4.6530385, -3.4083881, -3.0938363, 1.7179408, -3.3272557, 0.9561169, 0.3554761, 0.13326997, -1.0906507, -1.216253, 1.0336629, 1.1236805, -0.9689409, 0.5683843, 0.1861718, 0.23685807, 1.5890319, 1.0316361, 0.46518937, 0.86191344, -0.84835, 0.56682056, 1.3140951, -0.13236761, 0.42991808, 1.2670137, -0.77770096, 0.009323001, -0.32215795, 1.5236688, 3.8474588, 1.1774094, -1.0427856, 0.14818543, 0.72806954, 0.52160555, 1.2978964, 3.173862, 1.462686, 0.21574964, 1.2582943, 0.42488742, -0.63753575, 2.0299652, -0.2574278, 0.2562956, -0.19498685, 0.22289494, 0.55578184, 1.135375, -0.04183173, -1.0174584, 2.024195, 1.8950436, 3.2064705, 0.8659638, 2.1927743, 0.7894763, 0.99015695, 3.078844, 2.2428102, 2.2836294, 0.074686676, 2.6311154, 2.131141, 1.776381, 1.9604095, 1.9009273, 0.13236701, -0.4421916, 0.7504924, 1.2154832, -0.42112043, -0.28934568, 1.1821545, -1.2056537, 1.2468443, -0.67887145, 0.090064645, -0.11995959, -0.18719256, -0.099600814, -0.51897025, 1.5151548, 1.3506666, 1.3490187, 3.3809688, 0.9271738, 2.2142003, -0.6496841, 2.5934682, 1.0224643, 4.205883, 3.9734344, -0.31967682, 0.12812269, -0.9923417, -0.74067444, 0.02852571, -0.67645276, -0.84400666, 0.22376108, -0.5228683, 2.4571161, -1.063995, 0.79982543, 0.95303804, 1.3442445, -0.20842916, 1.6857667, -1.2380712, 1.4501462, -0.45005715, -1.152629, -0.59188163, 1.2426996, 0.526055, 0.9198674, -2.0879736, 1.6046958, -0.7270818, 0.77416897, -1.7310431, 0.1599561, 2.237581, 0.5214265, 0.4195066, 4.054694, 2.2938023, 1.0625987, -0.6568833, -1.0585979, 0.70337737, 1.3096178, 1.4538621, 0.50440544, -1.4165936, -1.2983577, 0.26294255, 0.07909961, 1.8013277, 0.027682543, 0.92637897, 0.47944468, 0.75180846, 4.094062, 1.6385992, 1.945972, -0.73010665, 0.0812588, -1.5758258, -0.27642596, -1.9834675, 2.6063437, -0.53067124, 1.2675405, 0.4320913, -0.048347592, -0.9566473, 2.2220378, 2.1621146, 2.952252, 0.83457994, -0.0033900142, -0.53659284, 0.98681706, -1.5374308, 1.9763281, -2.98258, 1.0986577, 1.1642288, -0.5455827, -1.3745713, 0.2565763, 0.1514723, 2.1277742, 1.2205718, 3.

In [0]:
predictions_df.write.mode("overwrite").parquet("/tmp/predictions")

In [0]:
result_df = spark.read.load("/tmp/predictions")

In [0]:
display(result_df)

content prediction /9j/4AAQSkZJRgABAQEASABIAAD/4iH8SUNDX1BST0ZJTEUAAQEAACHsTktPTgIgAABtbnRyUkdCIFhZWiAH2QACABQAEQAHAAphY3NwQVBQTAAAAABub25lAAAAAQAAAAAAAAAAAAAAAAAA9tYAAQAAAADTLQAAAAAAAAAAAAA= (truncated) List(1.7725176, 1.5770736, -2.6005592, -4.905384, -3.3790333, -1.9383128, -0.60205895, -0.197613, -0.18928075, 2.6218255, -0.50234866, 2.9826248, -0.35017857, -1.4919655, 0.6217473, 0.64147174, -1.8989611, -1.0708106, 0.73241657, -2.5698917, -0.46360493, 1.3014597, 1.9864749, -0.10609645, 3.4643447, 4.594158, 2.380334, 1.6286986, 2.528562, -3.2339952, 2.0352037, -1.0854582, -0.8066826, -1.7890975, 0.1262632, 1.740254, 2.0371528, 3.2759664, -1.2690675, 0.19193923, -0.44395652, -2.677982, -1.5153213, 0.49674007, -0.35637426, 3.195145, 0.62966096, 3.0667338, 0.781185, 1.3670173, 1.8256392, 0.5954966, -1.479928, -1.6697989, -0.054195225, 1.1609875, -1.3336691, -0.9130181, -0.5802858, -0.4931754, -0.99556625, 0.07373883, 1.044997, -2.4257038, 1.8397236, -2.7832828, -0.46932697, 0.51887107, -1.684916, -3.8083298, -0.26433784, -3.2416544, 2.3970397, 3.042668E-4, 2.7559204, -2.8508973, -0.42100918, 0.051429972, -1.7878013, -1.0414982, -2.5719452, -1.7337067, -0.7291219, -0.4774648, 0.8143737, 0.0065226555, -0.5673452, -2.4061995, 2.326864, 1.1267153, 1.0586907, -1.9578568, 0.12305617, 1.6415417, 0.66466516, -0.32577184, 0.6567751, -1.8466474, -4.920596, -0.917505, -2.3007884, -0.03603828, -1.9014257, 1.2262081, 0.68487847, -2.1935437, 0.15825069, 0.87938464, -1.7734747, -1.8111606, -1.6086483, -1.041224, -0.84098995, 0.83686906, 0.5676784, -1.289266, -1.9469901, -3.5954056, -0.50811917, -2.688472, -3.670728, -2.873859, -2.1177642, -3.8778353, -1.2435992, -2.4141426, -3.1271846, 0.8599884, -0.7303767, -0.48729515, -2.1587408, -0.06906229, 1.6534498, 1.0533633, 0.25611582, 1.6888733, -0.7751453, -2.138032, 0.9331051, -1.2752732, -0.9435465, -0.408939, -2.157826, -1.579575, -2.7162597, 0.064563274, -1.7323421, -2.3731158, -4.6530385, -3.4083881, -3.0938363, 1.7179408, -3.3272557, 0.9561169, 0.3554761, 0.13326997, -1.0906507, -1.216253, 1.0336629, 1.1236805, -0.9689409, 0.5683843, 0.1861718, 0.23685807, 1.5890319, 1.0316361, 0.46518937, 0.86191344, -0.84835, 0.56682056, 1.3140951, -0.13236761, 0.42991808, 1.2670137, -0.77770096, 0.009323001, -0.32215795, 1.5236688, 3.8474588, 1.1774094, -1.0427856, 0.14818543, 0.72806954, 0.52160555, 1.2978964, 3.173862, 1.462686, 0.21574964, 1.2582943, 0.42488742, -0.63753575, 2.0299652, -0.2574278, 0.2562956, -0.19498685, 0.22289494, 0.55578184, 1.135375, -0.04183173, -1.0174584, 2.024195, 1.8950436, 3.2064705, 0.8659638, 2.1927743, 0.7894763, 0.99015695, 3.078844, 2.2428102, 2.2836294, 0.074686676, 2.6311154, 2.131141, 1.776381, 1.9604095, 1.9009273, 0.13236701, -0.4421916, 0.7504924, 1.2154832, -0.42112043, -0.28934568, 1.1821545, -1.2056537, 1.2468443, -0.67887145, 0.090064645, -0.11995959, -0.18719256, -0.099600814, -0.51897025, 1.5151548, 1.3506666, 1.3490187, 3.3809688, 0.9271738, 2.2142003, -0.6496841, 2.5934682, 1.0224643, 4.205883, 3.9734344, -0.31967682, 0.12812269, -0.9923417, -0.74067444, 0.02852571, -0.67645276, -0.84400666, 0.22376108, -0.5228683, 2.4571161, -1.063995, 0.79982543, 0.95303804, 1.3442445, -0.20842916, 1.6857667, -1.2380712, 1.4501462, -0.45005715, -1.152629, -0.59188163, 1.2426996, 0.526055, 0.9198674, -2.0879736, 1.6046958, -0.7270818, 0.77416897, -1.7310431, 0.1599561, 2.237581, 0.5214265, 0.4195066, 4.054694, 2.2938023, 1.0625987, -0.6568833, -1.0585979, 0.70337737, 1.3096178, 1.4538621, 0.50440544, -1.4165936, -1.2983577, 0.26294255, 0.07909961, 1.8013277, 0.027682543, 0.92637897, 0.47944468, 0.75180846, 4.094062, 1.6385992, 1.945972, -0.73010665, 0.0812588, -1.5758258, -0.27642596, -1.9834675, 2.6063437, -0.53067124, 1.2675405, 0.4320913, -0.048347592, -0.9566473, 2.2220378, 2.1621146, 2.952252, 0.83457994, -0.0033900142, -0.53659284, 0.98681706, -1.5374308, 1.9763281, -2.98258, 1.0986577, 1.1642288, -0.5455827, -1.3745713, 0.2565763, 0.1514723, 2.1277742, 1.2205718, 3.